In [1]:
import warnings
warnings.filterwarnings('ignore')
import os
import sys
sys.path.append('..')

import urbanpy as up
import matplotlib.pyplot as plt
from tqdm.auto import tqdm

tqdm.pandas()

#usando a API para obter e manipular os dados
import geopandas as gpd

#path para a biblioteca do apiModulo. Ajuste de acordo com a necessidade
sys.path.insert(0, os.path.abspath('../'))
from apiModulo.api import *

In [2]:
#obtendo area de interesse
anel_viario = obterCamada('anel_viario')
slz = up.download.nominatim_osm('São Luís, Brasil')

In [14]:
#criando os hexagonos
hex_slz = up.geom.gen_hexagons(resolution=9, city=slz)

In [4]:
#pop_df = pd.read_csv('https://data.humdata.org/dataset/c17003d1-47f4-4ec5-8229-2f77aeb114be/resource/957218ee-c740-44c0-88e5-7faeef813a0c/download/population_bra_northeast_2018-10-01.csv.zip')
pop_df = pd.read_csv('../../exemplos/hdx_populacao/population_bra_northeast_2018-10-01.csv')

In [6]:
pop_gdf = gpd.GeoDataFrame(
    pop_df, geometry=gpd.points_from_xy(pop_df.longitude, pop_df.latitude))

In [11]:
hex_slz_gdf = up.geom.merge_shape_hex(hex_slz, pop_gdf, agg={'population_2020': 'sum'})

In [15]:
hex_slz_gdf.head()

hex                                           geometry  \
0  89800d5b3d7ffff  POLYGON ((-44.42828 -2.74363, -44.42725 -2.741...   
1  89800c2eb97ffff  POLYGON ((-44.39663 -2.79418, -44.39559 -2.792...   
2  898008954cbffff  POLYGON ((-44.25322 -2.64758, -44.25218 -2.645...   
3  89800896563ffff  POLYGON ((-44.36451 -2.69167, -44.36348 -2.689...   
4  89800895cc7ffff  POLYGON ((-44.29981 -2.59845, -44.29878 -2.596...   

   population_2020  
0              NaN  
1              NaN  
2          1.49771  
3              NaN  
4              NaN

In [13]:
visMapaGJson(hex_slz_gdf, 
                    variavel='population_2020', 
                    descricao='HDX densidade populacional',  
                    height='800', 
                    width='90%')

In [16]:
hex_slz_gdf = hex_slz_gdf.reset_index()
hex_slz_gdf['cod_camada'] = hex_slz_gdf.index

In [17]:
inserirCamada(
    dado = hex_slz_gdf,
    tabela= 'hdx_populacao_2020',
    campo_chave='cod_camada',
    nome='hdx_populacao_2020',
    descricao='HEX Hdx Densidade Populacional 2020'
)